# Real voltage and voltage phasor

$$
v(z,t) = \text{Re}(V(z) e^{j \omega t}) \\
V(z) = V_0^+ e^{- \gamma z} + V_0^- e^{\gamma z} \\
\gamma = \alpha + j\beta = \text{complex propagation constant (m}^{-1}\text{)} \\
\omega = 2\pi f \\
f = \text{Frequency (Hz)} \\
\beta = 2 \pi / \lambda \\
\lambda = v / f = \text{wavelength (m)} \\
v = \text{velocity (m/s)}
$$

But really, the expression for the voltage phasor is:

$$
V(z) = V_0^+ e^{- \gamma (z + l)} + V_0^- e^{\gamma (z - l)}
$$

Why?

In [1]:
import matplotlib
print(matplotlib.__version__)

import cmath as cm
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
%matplotlib notebook
# %matplotlib inline
from IPython.display import HTML
plt.ioff()

3.3.2


In [2]:
freq_Hz = 1e8
velocity_mps = 2e8
wavelength_m = velocity_mps / freq_Hz
period_s = 1. / freq_Hz

omega = 2 * np.pi * freq_Hz
alpha = 0
beta = 2 * np.pi / wavelength_m
gamma = complex(alpha, beta)
refl_coef = complex(0.5, 0)
V_0_plus = 1.0
V_0_minus = refl_coef * V_0_plus

print(f" Frequency: {freq_Hz:,} (Hz)")
print(f"  Velocity: {velocity_mps:,} (m/s)")
print(f"Wavelength: {wavelength_m:,} (m)")
print(f"    Period: {period_s} (s)")
print()
print(f"     omega: {omega} (rad/s)")
print(f"     alpha: {alpha} (1/m)")
print(f"      beta: {beta} (1/m)")
print(f"     gamma: {gamma} (1/m)")

tline_length = 2 * wavelength_m
numpnts_z = 201
z = np.linspace(-tline_length, 0, numpnts_z)

t_max = period_s
numpnts_t = 100
t = np.linspace(0, t_max, numpnts_t, endpoint=False)

vexp = np.vectorize(cm.exp)
vsqrt = np.vectorize(cm.sqrt)

phasor_forward = V_0_plus  * vexp(-gamma * (z + tline_length))
phasor_reverse = V_0_minus * vexp( gamma * (z - tline_length))
phasor = phasor_forward + phasor_reverse
         
vsw = np.real(vsqrt(phasor * np.conj(phasor)))

fig, ax = plt.subplots()
ax.set_xlabel('Distance (m)')
ax.set_ylabel('Amplitude')
ax.set_xlim(-tline_length, 0)
ylim = max(np.absolute(V_0_plus), np.absolute(V_0_minus))
ax.set_ylim(-2*ylim, 2*ylim)
ax.grid()

ax.plot(z, vsw)
exp_j_omega_t = vexp(complex(0, 1) * omega * t[0])
real_forward = np.real(phasor_forward * exp_j_omega_t)
real_reverse = np.real(phasor_reverse * exp_j_omega_t)
line_forward, = ax.plot(z, real_forward)
line_reverse, = ax.plot(z, real_reverse)
line_total, = ax.plot(z, real_forward + real_reverse)

def calc_lines_for_next_time_step(i):
    exp_j_omega_t = vexp(complex(0, 1) * omega * t[i])
    real_forward = np.real(phasor_forward * exp_j_omega_t)
    real_reverse = np.real(phasor_reverse * exp_j_omega_t)

    line_forward.set_ydata(real_forward)  # update line_forward data.
    line_reverse.set_ydata(real_reverse)  # update line_reverse data.
    line_total.set_ydata(real_forward + real_reverse)  # update line_total data.
    return [line_forward, line_reverse, line_total]


ani = FuncAnimation(
    fig, calc_lines_for_next_time_step, interval=20, blit=True, save_count=numpnts_t)

HTML(ani.to_jshtml())

 Frequency: 100,000,000.0 (Hz)
  Velocity: 200,000,000.0 (m/s)
Wavelength: 2.0 (m)
    Period: 1e-08 (s)

     omega: 628318530.7179586 (rad/s)
     alpha: 0 (1/m)
      beta: 3.141592653589793 (1/m)
     gamma: 3.141592653589793j (1/m)
